# Backtesting.py Library Tutorial

## Introduction to Backtesting.py

Backtesting.py is a Python framework for inferring viability of trading strategies on historical data. It provides a simple, fast, and flexible way to backtest trading strategies with just a few lines of code.

### Key Features:
- Simple and intuitive API
- Fast vectorized operations
- Built-in performance metrics
- Interactive charts and plots
- Support for various order types
- Portfolio optimization capabilities

## Installation

## Basic Imports and Setup

In [2]:
import pandas as pd
import numpy as np
from backtesting import Backtest, Strategy
from backtesting.lib import crossover
from backtesting.test import SMA, GOOG  # Sample data and indicators
import warnings
warnings.filterwarnings('ignore')

# Display all columns in pandas
pd.set_option('display.max_columns', None)

/Users/alex/Dev/cryptoTraining/venv/lib/python3.13/site-packages/backtesting/_plotting.py:55: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support, such as old IDEs. Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

## Understanding the Data Format

In [3]:
# Load sample Google stock data
data = GOOG.copy()
print("Data structure:")
print(data.head())
print(f"\nData shape: {data.shape}")
print(f"Date range: {data.index[0]} to {data.index[-1]}")

Data structure:
              Open    High     Low   Close    Volume
2004-08-19  100.00  104.06   95.96  100.34  22351900
2004-08-20  101.01  109.08  100.50  108.31  11428600
2004-08-23  110.75  113.48  109.05  109.40   9137200
2004-08-24  111.24  111.60  103.57  104.87   7631300
2004-08-25  104.96  108.00  103.88  106.00   4598900

Data shape: (2148, 5)
Date range: 2004-08-19 00:00:00 to 2013-03-01 00:00:00


**Required Data Format:**
- DataFrame with DateTime index
- Columns: 'Open', 'High', 'Low', 'Close', 'Volume' (OHLCV)
- Data should be sorted chronologically

## Creating Your First Strategy

In [ ]:
class SMACrossStrategy(Strategy):
    """
    Simple Moving Average Crossover Strategy
    Buy when fast SMA crosses above slow SMA
    Sell when fast SMA crosses below slow SMA
    """
    
    # Strategy parameters
    fast_sma = 10
    slow_sma = 30
    
    def init(self):
        """Initialize indicators"""
        # Calculate moving averages
        self.sma_fast = self.I(SMA, self.data.Close, self.fast_sma)
        self.sma_slow = self.I(SMA, self.data.Close, self.slow_sma)
    
    def next(self):
        """Define trading logic for each bar"""
        # Buy signal: fast SMA crosses above slow SMA
        if crossover(self.sma_fast, self.sma_slow):
            self.buy()
        
        # Sell signal: fast SMA crosses below slow SMA
        elif crossover(self.sma_slow, self.sma_fast):
            self.sell()

print("Strategy class created successfully!")

## Running a Backtest

In [ ]:
# Create and run backtest
bt = Backtest(data, SMACrossStrategy, cash=10000, commission=.002)
results = bt.run()

# Display results
print("Backtest Results:")
print(results)

## Key Strategy Methods

### The `init()` Method

In [260]:
def init(self):
    """
    Called once at the beginning of backtesting
    Used to:
    - Initialize indicators using self.I()
    - Set up any variables needed throughout the strategy
    - Prepare data transformations
    """
    self.sma = self.I(SMA, self.data.Close, 20)
    # self.rsi = self.I(lambda x, n: RSI(x, n), self.data.Close, 14)

### The `next()` Method

In [261]:
def next(self):
    """
    Called for each bar of data
    Contains the main trading logic
    Available methods:
    - self.buy() / self.sell() - Market orders
    - self.position - Current position info
    - self.data - Current price data
    """
    if self.data.Close[-1] > self.sma[-1]:
        self.buy()
    elif self.data.Close[-1] < self.sma[-1]:
        self.sell()

## Position Management

In [262]:
class PositionSizingStrategy(Strategy):
    def init(self):
        self.sma = self.I(SMA, self.data.Close, 20)
    
    def next(self):
        # Check current position
        if not self.position:  # No position
            if self.data.Close[-1] > self.sma[-1]:
                # Buy with specific size (50% of equity)
                self.buy(size=0.5)
        
        elif self.position.is_long:  # Long position
            if self.data.Close[-1] < self.sma[-1]:
                self.position.close()  # Close position
        
        # Access position information
        if self.position:
            print(f"Position size: {self.position.size}")
            print(f"Position value: {self.position.pl}")

## Advanced Order Types

In [263]:
class AdvancedOrderStrategy(Strategy):
    def init(self):
        self.sma = self.I(SMA, self.data.Close, 20)
    
    def next(self):
        current_price = self.data.Close[-1]
        
        # Market order
        if current_price > self.sma[-1] and not self.position:
            self.buy()
        
        # Limit order (buy below current price)
        elif not self.position:
            self.buy(limit=current_price * 0.98)
        
        # Stop-loss order
        elif self.position.is_long:
            self.sell(stop=current_price * 0.95)
        
        # Take-profit order
        elif self.position.is_long:
            self.sell(limit=current_price * 1.10)

## Performance Metrics

In [ ]:
# Run backtest and analyze results
bt = Backtest(data, SMACrossStrategy, cash=10000, commission=.002)
results = bt.run()

print("Key Performance Metrics:")
print(f"Total Return: {results['Return [%]']:.2f}%")
print(f"Buy & Hold Return: {results['Buy & Hold Return [%]']:.2f}%")
print(f"Max Drawdown: {results['Max. Drawdown [%]']:.2f}%")
print(f"Sharpe Ratio: {results['Sharpe Ratio']:.2f}")
print(f"Number of Trades: {results['# Trades']}")
print(f"Win Rate: {results['Win Rate [%]']:.2f}%")

## Visualization

In [ ]:
# Plot backtest results
bt.plot(show_legend=False, resample=False, plot_pl=True, relative_equity=False)

# The plot includes:
# - Price chart with entry/exit points
# - Portfolio equity curve
# - Drawdown periods
# - Trade markers

## Parameter Optimization

In [ ]:
# Optimize strategy parameters
optimization_results = bt.optimize(
    fast_sma=range(5, 20, 2),     # Test fast SMA from 5 to 18
    slow_sma=range(20, 50, 5),    # Test slow SMA from 20 to 45
    maximize='Sharpe Ratio',       # Optimization objective
    constraint=lambda p: p.fast_sma < p.slow_sma  # Constraint
)

print("Optimal Parameters:")
print(optimization_results)

## Complete Example: RSI Strategy

In [ ]:
def RSI(close, period=14):
    """Calculate RSI indicator - fixed for backtesting library"""
    # Convert to pandas Series if it's an _Array object
    if hasattr(close, '__array__'):
        close = pd.Series(close)
    
    delta = close.diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=period).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=period).mean()
    rs = gain / loss
    rsi = 100 - (100 / (1 + rs))
    
    # Return as numpy array for backtesting compatibility
    return rsi.values

class RSIStrategy(Strategy):
    """
    RSI Mean Reversion Strategy
    Buy when RSI < 30 (oversold)
    Sell when RSI > 70 (overbought)
    """
    
    rsi_period = 14
    oversold = 30
    overbought = 70
    
    def init(self):
        self.rsi = self.I(RSI, self.data.Close, self.rsi_period)
    
    def next(self):
        # Buy when oversold and no position
        if self.rsi[-1] < self.oversold and not self.position:
            self.buy()
        
        # Sell when overbought and have long position
        elif self.rsi[-1] > self.overbought and self.position.is_long:
            self.position.close()

# Run RSI strategy
bt_rsi = Backtest(data, RSIStrategy, cash=10000, commission=.002)
results_rsi = bt_rsi.run()

print("RSI Strategy Results:")
print(f"Return: {results_rsi['Return [%]']:.2f}%")
print(f"Sharpe Ratio: {results_rsi['Sharpe Ratio']:.2f}")

## Best Practices and Tips

### 1. Data Quality

In [ ]:
# Always check for data issues
def validate_data(df):
    print(f"Missing values: {df.isnull().sum().sum()}")
    print(f"Duplicate dates: {df.index.duplicated().sum()}")
    
    # Check for unrealistic price movements
    returns = df['Close'].pct_change()
    extreme_moves = returns[abs(returns) > 0.2]
    if len(extreme_moves) > 0:
        print(f"Extreme price movements detected: {len(extreme_moves)}")

validate_data(data)

### 2. Avoiding Look-Ahead Bias

In [269]:
# WRONG - Uses future data
def bad_strategy_next(self):
    if self.data.Close[-1] > self.data.Close[0:].mean():  # Uses all data
        self.buy()

# CORRECT - Only uses past data
def good_strategy_next(self):
    if self.data.Close[-1] > self.data.Close[:-1].mean():  # Excludes current bar
        self.buy()

### 3. Transaction Costs

In [270]:
# Always include realistic transaction costs
bt = Backtest(
    data, 
    Strategy, 
    cash=10000,
    commission=0.002,  # 0.2% per trade
    trade_on_close=True,  # More realistic execution
    exclusive_orders=True  # Prevent multiple orders per bar
)

## Common Pitfalls to Avoid

1. **Overfitting**: Don't optimize too many parameters
2. **Look-ahead bias**: Only use historical data available at each point
3. **Survivorship bias**: Include delisted stocks in your universe
4. **Ignoring transaction costs**: Always include realistic fees
5. **In-sample testing**: Always test on out-of-sample data

## Next Steps

- Explore more complex strategies (multi-asset, machine learning)
- Learn about walk-forward analysis
- Study risk management techniques
- Implement portfolio-level backtesting
- Use alternative data sources

## Resources

- [Official Documentation](https://kernc.github.io/backtesting.py/)
- [GitHub Repository](https://github.com/kernc/backtesting.py)
- [Example Strategies](https://kernc.github.io/backtesting.py/doc/examples/)

Happy backtesting! 📈